In [1]:
import cadquery as cq
from jupyter_cadquery import set_defaults, set_sidecar, get_defaults
from jupyter_cadquery.cadquery import show, PartGroup, Part, Faces, Edges
from cadquery_massembly import Mate, MAssembly, relocate
from jupyter_cadquery.cad_animation import Animation

set_defaults(axes=True, axes0=True, edge_accuracy=0.01, mate_scale=5, zoom=3, theme="light",cad_width=600, height=500, timeit=False)
#set_sidecar("Hexapod", init=True)


Overwriting auto display for cadquery Workplane and Shape


# Hexapod 

![2-hexapod.png](2-hexapod.png)

In [2]:
import numpy as np
horizontal_angle = 25

def intervals(count):
    r = [ min(180, (90 + i*(360 // count)) % 360) for i in range(count)]
    return r 

def times(end, count):
    return np.linspace(0, end, count+1)
    
def vertical(count, end, offset, reverse):
    ints = intervals(count)
    heights = [round(35 * np.sin(np.deg2rad(x)) - 15, 1) for x in ints]
    heights.append(heights[0])
    return times(end, count), heights[offset:] + heights[1:offset+1]

def horizontal(end, reverse):
    factor = 1 if reverse else -1
    return times(end, 4), [0, factor * horizontal_angle, 0, -factor * horizontal_angle, 0]

print("Leg group 1 (transparent)")
print("horizontal movement    ", horizontal(4, True))
print("vertical heights (left) ", vertical(8, 4, 0, True))
print("vertical heights (right)", vertical(8, 4, 0, False))

print("\nLeg group 1 (filled)")
print("horizontal movement", horizontal(4, False))
print("vertical heights (left) ", vertical(8, 4, 4, True))
print("vertical heights (right)", vertical(8, 4, 4, False))


Leg group 1 (transparent)
horizontal movement     (array([0., 1., 2., 3., 4.]), [0, 25, 0, -25, 0])
vertical heights (left)  (array([0. , 0.5, 1. , 1.5, 2. , 2.5, 3. , 3.5, 4. ]), [20.0, 9.7, -15.0, -15.0, -15.0, -15.0, -15.0, 9.7, 20.0])
vertical heights (right) (array([0. , 0.5, 1. , 1.5, 2. , 2.5, 3. , 3.5, 4. ]), [20.0, 9.7, -15.0, -15.0, -15.0, -15.0, -15.0, 9.7, 20.0])

Leg group 1 (filled)
horizontal movement (array([0., 1., 2., 3., 4.]), [0, -25, 0, 25, 0])
vertical heights (left)  (array([0. , 0.5, 1. , 1.5, 2. , 2.5, 3. , 3.5, 4. ]), [-15.0, -15.0, -15.0, 9.7, 20.0, 9.7, -15.0, -15.0, -15.0])
vertical heights (right) (array([0. , 0.5, 1. , 1.5, 2. , 2.5, 3. , 3.5, 4. ]), [-15.0, -15.0, -15.0, 9.7, 20.0, 9.7, -15.0, -15.0, -15.0])


# Assembly

## Parts

In [3]:
thickness = 2
height = 40
width = 65
length = 100
diam = 4
tol = 0.05

In [4]:
def create_base(rotate=False):
    x1, x2 = 0.63, 0.87
    base_holes = {
        "right_back": (-x1*length, -x1*width), "right_middle": (0, -x2*width), "right_front": ( x1*length, -x1*width),
        "left_back":  (-x1*length,  x1*width), "left_middle":  (0,  x2*width), "left_front":  ( x1*length,  x1*width),
    }
    stand_holes = {"front_stand": (0.75 * length, 0), "back_stand": (-0.8 * length, 0)}

    workplane = cq.Workplane()
    if rotate:
        workplane = workplane.transformed(rotate=(30, 45, 60))
        
    base = (workplane
        .ellipseArc(length, width, 25, -25, startAtCurrent=False).close()
        .pushPoints(list(base_holes.values())).circle(diam / 2 + tol)
        .moveTo(*stand_holes["back_stand" ]).rect(thickness + 2 * tol, width / 2 + 2 * tol)
        .moveTo(*stand_holes["front_stand"]).rect(thickness + 2 * tol, width / 2 + 2 * tol)
        .extrude(thickness)
    )
    base

    # tag mating points
    if rotate:
        l_coord = lambda vec2d: workplane.plane.toWorldCoords(vec2d).toTuple()
        l_nps = lambda vec2d: cq.NearestToPointSelector(l_coord(vec2d))

        base.faces(f"<{l_coord((0,0,1))}").tag("bottom")
        base.faces(f">{l_coord((0,0,1))}").tag("top")
        
        for name, hole in base_holes.items():
            base.faces(f"<{l_coord((0,0,1))}").edges(l_nps(hole)).tag(name)

        for name, hole in stand_holes.items():
            base.faces(f"<{l_coord((0,0,1))}").wires(l_nps(hole)).tag(name)
    else:
        base.faces("<Z").tag("bottom")
        base.faces(">Z").tag("top")
        
        for name, hole in base_holes.items():
            base.faces("<Z").wires(cq.NearestToPointSelector(hole)).tag(name)

        for name, hole in stand_holes.items():
            base.faces("<Z").wires(cq.NearestToPointSelector(hole)).tag(name)

    return base

base_holes_names = {"right_back", "right_middle", "right_front", "left_back", "left_middle", "left_front"}

In [5]:
def create_stand():
    stand = cq.Workplane().box(height, width / 2 + 10, thickness)
    inset = cq.Workplane().box(thickness, width / 2, thickness)
    backing = cq.Workplane("ZX").polyline([(10,0), (0,0), (0, 10)]).close().extrude(thickness)

    stand = (stand
        .union(inset.translate(( (height + thickness) / 2, 0, 0)))
        .union(inset.translate((-(height + thickness) / 2, 0, 0)))
        .union(backing.translate((-height / 2, -thickness / 2, thickness / 2)))
        .union(backing.rotate((0, 0, 0), (0, 1, 0), -90).translate((height / 2, -thickness / 2, thickness / 2)))
    )
    return stand

stand_names = ("front_stand", "back_stand")

In [6]:
def create_upper_leg():
    l1, l2 = 50, 80
    pts = [( 0,  0), ( 0, height/2), (l1, height/2 - 5), (l2, 0)]
    upper_leg_hole = (l2 - 10, 0)

    upper_leg = (cq.Workplane()
        .polyline(pts).mirrorX()
        .pushPoints([upper_leg_hole]).circle(diam/2 + tol).extrude(thickness)
        .edges("|Z and (not <X)").fillet(4)
    )

    axle = (cq.Workplane("XZ", origin=(0, height/2 + thickness + tol, thickness/2))
        .circle(diam/2).extrude(2 * (height/2 + thickness + tol))
    )

    upper_leg = upper_leg.union(axle)

    # tag mating points
    upper_leg.faces(">Z").edges(cq.NearestToPointSelector(upper_leg_hole)).tag("top")
    upper_leg.faces("<Z").edges(cq.NearestToPointSelector(upper_leg_hole)).tag("bottom")

    return upper_leg

def create_lower_leg():
    w, l1, l2 = 15, 20, 120
    pts = [( 0,  0), ( l1, w), (l2, 0)]
    lower_leg_hole = (l1 - 10, 0)

    lower_leg = (cq.Workplane()
        .polyline(pts).mirrorX()
        .pushPoints([lower_leg_hole]).circle(diam/2 + tol)
        .extrude(thickness)
        .edges("|Z").fillet(5)
    )

    # tag mating points
    lower_leg.faces(">Z").edges(cq.NearestToPointSelector(lower_leg_hole)).tag("top"),
    lower_leg.faces("<Z").edges(cq.NearestToPointSelector(lower_leg_hole)).tag("bottom")
    
    return lower_leg

leg_angles = {
    "right_back": -105,  "right_middle":-90, "right_front":-75, 
    "left_back":   105,  "left_middle":  90, "left_front":  75,
    
}
leg_names = list(leg_angles.keys())

In [7]:
base = create_base(rotate=False)
stand = create_stand()
upper_leg = create_upper_leg()
lower_leg = create_lower_leg()

d = show(
    base, 
    stand.translate((0,100,thickness/2)), 
    upper_leg.translate((-100,-100,0)),
    lower_leg.translate((0,-100,0))
)
d.cq_view.renderer.controls[0].rotateSpeed = 0.30
d.cq_view.renderer.controls[0].panSpeed = 0.30
d.cq_view.renderer.controls[0].zoomSpeed = 0.30

## Define Assembly

In [8]:
def create_hexapod():
    # Some shortcuts
    L = lambda *args: cq.Location(cq.Vector(*args))
    C = lambda *args: cq.Color(*args)

    # Leg assembly
    leg = (MAssembly(upper_leg, name="upper", color=C("orange"))
        .add(lower_leg, name="lower", color=C("orange"), loc=L(80,0,0))
    )
    # Hexapod assembly
    hexapod = (MAssembly(base, name="bottom", color=C("gray"), loc=L(0, 1.1*width, 0))
        .add(base, name="top", color=C("gray"), loc=L(0, -2.2*width, 0))
        .add(stand, name="front_stand", color=C(0.5, 0.8, 0.9), loc=L( 40, 100, 0))
        .add(stand, name="back_stand", color=C(0.5, 0.8, 0.9), loc=L(-40, 100, 0))
    )
    
    for i, name in enumerate(leg_names):
        hexapod.add(leg, name=name, loc=L(100, -55*(i-1.7), 0))

    return hexapod

## Define Mates 

In [9]:
from collections import OrderedDict as odict

hexapod = create_hexapod()

hexapod.mate("bottom?top", name="bottom", origin=True)
hexapod.mate("top?bottom", name="top", origin=True, transforms=odict(rx=180, tz=-(height + 2 * tol)))

for name in stand_names:
    hexapod.mate(f"bottom?{name}", name=f"{name}_bottom", transforms=odict(rz=-90 if "f" in name else 90))
    hexapod.mate(f"{name}@faces@<X", name=name, origin=True, transforms=odict(rx=180))

for name in base_holes_names:
    hexapod.mate(f"bottom?{name}", name=f"{name}_hole", transforms=odict(rz=leg_angles[name]))

for name in leg_names:
    lower, upper, angle = ("top", "bottom", -75) if "left" in name else ("bottom", "top", -75)
    hexapod.mate(f"{name}?{upper}", name=f"leg_{name}_hole", transforms=odict(rz=angle))
    hexapod.mate(f"{name}@faces@<Y", name=f"leg_{name}_hinge", origin=True, transforms=odict(rx=180, rz=-90))
    hexapod.mate(f"{name}/lower?{lower}", name=f"leg_{name}_lower_hole", origin=True)

show(hexapod, render_mates=False, axes=False, timeit=False)

## Relocate and assemble

In [10]:
relocate(hexapod)
show(hexapod, render_mates=True)

In [11]:
for leg in leg_names:
    hexapod.assemble(f"leg_{leg}_lower_hole", f"leg_{leg}_hole")
    hexapod.assemble(f"leg_{leg}_hinge", f"{leg}_hole")

hexapod.assemble("top", "bottom")

for stand_name in stand_names:
    hexapod.assemble(f"{stand_name}", f"{stand_name}_bottom")


d = show(hexapod, render_mates=True, grid=True, axes=False)

In [21]:
import json
from jupyter_cadquery.cadquery.cad_objects import to_assembly
from jupyter_cadquery.cad_objects import _combined_bb
from jupyter_cadquery import get_default
from jupyter_cadquery.ocp_utils import BoundingBox

preset = lambda key, value: get_default(key) if value is None else value

def convert_assembly(assy, file):
    
    def _combined_bb(shapes):
        def c_bb(shapes, bb):
            for shape in shapes["parts"]:
                if shape.get("parts") is None:
                    if bb is None:
                        bb = BoundingBox(shape["bb"])
                    else:
                        bb.update(shape["bb"])
                else:
                    return c_bb(shape, bb)
            return bb

        bb = c_bb(shapes, None)
        return bb
    
    def default(obj):
        if type(obj).__module__ == np.__name__:
            if isinstance(obj, np.ndarray):
                return obj.tolist()
            else:
                return obj.item()
        raise TypeError('Unknown type:', type(obj))

    part_group = to_assembly(assy)
    if len(part_group.objects) == 1 and isinstance(part_group.objects[0], PartGroup):
        part_group = part_group.objects[0]
    mapping = part_group.to_state()
    shapes = part_group.collect_mapped_shapes(
        mapping,
        quality=preset("quality", get_default("quality")),
        deviation=preset("deviation", get_default("deviation")),
        angular_tolerance=preset("angular_tolerance", get_default("angular_tolerance")),
        edge_accuracy=preset("edge_accuracy", get_default("edge_accuracy")),
        render_edges=preset("render_edges", get_default("render_edges")),
        render_normals=preset("render_normals", get_default("render_normals")),
        progress=d.progress,
        timeit=False,
    )
    tree = part_group.to_nav_dict()
    
    data = dict(shapes=shapes, mapping=mapping, tree=tree, bb=_combined_bb(shapes).to_dict())

    with open(f"/tmp/{file}.js", "w") as fd:
        fd.write("const example = ")
        fd.write(json.dumps(data, default=default)) 
        fd.write("\nexport { example }")

In [22]:
convert_assembly(hexapod, "hexapod")


In [56]:
from cadquery.occ_impl.assembly import toJSON
import json

j = toJSON(hexapod)
with open("/tmp/hexapod.json", "w") as fd:
    fd.write(json.dumps(j))


ImportError: cannot import name 'toJSON' from 'cadquery.occ_impl.assembly' (/opt/anaconda/envs/jc22/lib/python3.8/site-packages/cadquery/occ_impl/assembly.py)

In [54]:
from cadquery import Location, Compound
from cadquery.occ_impl.exporters.vtk import toString

def toJSON(
    assy,
    loc = Location(),
    color = (1.0, 1.0, 1.0, 1.0),
    tolerance = 1e-3,
    path = ""
):

    loc = loc * assy.loc
    trans, rot = loc.toTuple()
    path = f"{path}/{assy.name}"
    
    if assy.color:
        color = assy.color.toTuple()

    rv = {}

    if assy.shapes:
        data = toString(Compound.makeCompound(assy.shapes), tolerance)

        rv["shape"] = data
        rv["name"] = path
        rv["color"] = color
        rv["position"] = trans
        rv["orientation"] = rot
    
    rv["children"] = []
    for child in assy.children:
        rv["children"].append(toJSON(child, loc, color, tolerance, path))

    return rv

In [55]:
toJSON(hexapod)

{'name': '/bottom',
 'color': (0.527114987373352, 0.527114987373352, 0.527114987373352, 1.0),
 'position': (0.0, 0.0, 0.0),
 'orientation': (0.0, -0.0, 0.0),
 'children': [{'name': '/bottom/top',
   'color': (0.527114987373352, 0.527114987373352, 0.527114987373352, 1.0),
   'position': (0.0, 0.0, 0.0),
   'orientation': (0.0, -0.0, 0.0),
   'children': []},
  {'name': '/bottom/front_stand',
   'color': (0.5, 0.800000011920929, 0.8999999761581421, 1.0),
   'position': (76.6299303684197, 1.3404072159790126e-14, -2.0),
   'orientation': (-3.944304526105059e-31, -0.0, -3.141592653589793),
   'children': []},
  {'name': '/bottom/back_stand',
   'color': (0.5, 0.800000011920929, 0.8999999761581421, 1.0),
   'position': (-78.3700696315803, 1.3404072159790126e-14, -2.0),
   'orientation': (-3.944304526105059e-31, -0.0, -6.123233995736757e-17),
   'children': []},
  {'name': '/bottom/right_back',
   'color': (1.0, 0.37626200914382935, 0.0, 1.0),
   'position': (-61.37006963158031, -40.95, -2.0)

In [51]:
with open("/tmp/hexapod.json", "w") as fd:
    fd.write(json.dumps(toJSON(hexapod)))

In [14]:
%%time
j = toJSON(hexapod)
def pp(jassy, ind=""):
    for j in jassy:
        if isinstance(j, dict):
            print(ind, j["name"])
        else:
            pp(j, ind + "  ")
pp(j)

 bottom
   top
   front_stand
   back_stand
   right_back
     lower
   right_middle
     lower
   right_front
     lower
   left_back
     lower
   left_middle
     lower
   left_front
     lower
CPU times: user 500 ms, sys: 9.38 ms, total: 509 ms
Wall time: 503 ms


## Animation

In [15]:
leg_group = ("left_front", "right_middle", "left_back")

animation = Animation(d.root_group)

for name in leg_names:
    # move upper leg
    animation.add_track(f"bottom/{name}", "rz", *horizontal(4, "middle" in name))
    
    # move lower leg
    animation.add_track(f"bottom/{name}/lower", "rz", *vertical(8, 4, 0 if name in leg_group else 4, "left" in name))
    
    # lift hexapod to run on grid
    # animation.add_track(f"bottom", "tz", [0, 4], [61.25]*2)
    
animation.animate(speed=1)

AnimationAction(clip=AnimationClip(tracks=(QuaternionKeyframeTrack(name='bottom\\right_back.quaternion', times…

Export the above view to HTML

In [16]:
from ipywidgets.embed import embed_minimal_html, dependency_state
embed_minimal_html(
    'export.html', 
    title='Box', 
    views=[d.cq_view.renderer], 
    state=dependency_state(d.cq_view.renderer))